In [ ]:
%matplotlib inline



# Compare topographies

.. currentmodule:: eelbrain

This example shows how to compare EEG topographies, based on the method described by McCarthy & Wood [1]_.


In [ ]:
# sphinx_gallery_thumbnail_number = 4
from eelbrain import *

## Simulated data
Generate a simulated dataset (as in the `exa-cluster-based-mu` example)



In [ ]:
dss = []
for subject in range(10):
    # generate data for one subject
    ds = datasets.simulate_erp(seed=subject)
    # average across trials to get condition means
    ds_agg = ds.aggregate('cloze_cat')
    # add the subject name as variable
    ds_agg[:, 'subject'] = f'S{subject:02}'
    dss.append(ds_agg)

ds = combine(dss)
# make subject a random factor (to treat it as random effect for ANOVA)
ds['subject'].random = True
# Re-reference the EEG data (i.e., subtract the mean of the two mastoid channels):
ds['eeg'] -= ds['eeg'].mean(sensor=['M1', 'M2'])
print(ds.head())

The simulated data in the two conditions:



In [ ]:
p = plot.TopoArray('eeg', 'cloze_cat', ds=ds, axh=2, axw=10, t=[0.120, 0.200, 0.280])

## Test between conditions

Test whether the 120 ms topography differs between the two cloze conditions. The dataset already includes one row per cell (i.e., per cloze condition and subject). Consequently, we can just index the topography at the desired time point:



In [ ]:
topography = ds['eeg'].sub(time=0.120)
# normalize the data in accordance with McCarth & Wood (1985)
topography = normalize_in_cells(topography, 'sensor', 'cloze_cat', ds)
# "melt" the topography NDVar to turn the sensor dimension into a Factor
ds_topography = table.melt_ndvar(topography, 'sensor', ds=ds)
# Note EEG is a single column, and the last column indicates the sensor 
ds_topography.head()

ANOVA to test whether the effect of `cloze_cat` differs between sensors:



In [ ]:
test.ANOVA('eeg', 'cloze_cat * sensor * subject', ds=ds_topography)

The non-significant interaction suggests that the effect of `cloze_cat` does not differ between sensors, i.e., the topographies do not differ, which is consistent with being generated by the same underlying neural sources.


## Test two time points
Since we're not interested in condition here, we first average across conditions, i.e., with the goal of having one row per subject:



In [ ]:
ds_average = ds.aggregate('subject', drop_bad=True)
print(ds_average)

In order to compare two time points, we need to construct a new dataset with time point as :class:`Factor`:



In [ ]:
dss = []
for time in [0.120, 0.280]:
    ds_time = ds_average['subject',]  # A new dataset with the 'subject' variable only
    ds_time['eeg'] = ds_average['eeg'].sub(time=time)
    ds_time[:, 'time'] = f'{time*1000:.0f} ms'
    dss.append(ds_time)
ds_times = combine(dss)
ds_times.summary()

Then, normalize the data in accordance with McCarth & Wood (1985)



In [ ]:
topography = normalize_in_cells('eeg', 'sensor', 'time', ds=ds_times)
# "melt" the topography NDVar to turn the sensor dimension into a Factor
ds_topography = table.melt_ndvar(topography, 'sensor', ds=ds_times)
# Note EEG is a single column, and the last column indicates the sensor 
ds_topography.head()

Plot the topographies before and after normalization:



In [ ]:
p = plot.Topomap('eeg', 'time', ds=ds_times, ncol=2, title="Original")
p = plot.Topomap(topography, 'time', ds=ds_times, ncol=2, title="Normalized")

Compre the topographies with the ANOVA -- test whether the effect of time differs between sensors:



In [ ]:
test.ANOVA('eeg', 'time * sensor * subject', ds=ds_topography)

Visualize the difference



In [ ]:
res = testnd.TTestRelated(topography, 'time', match='subject', ds=ds_times)
p = plot.Topomap(res, ncol=3, title="Normalized topography differences")

## References
.. [1] McCarthy, G., & Wood, C. C. (1985). Scalp Distributions of Event-Related Potentials—An Ambiguity Associated with Analysis of Variance Models. Electroencephalography and Clinical Neurophysiology, 61, S226–S227. `10.1016/0013-4694(85)90858-2 <https://doi.org/10.1016/0013-4694(85)90858-2>`_


